In [1]:
from PIL import Image
import os
import cv2
import random
import math
import numpy as np
import albumentations as A
import matplotlib.pyplot as plt
import json
from ultralytics.data.converter import convert_segment_masks_to_yolo_seg


WARNING ⚠️ Python>=3.10 is required, but Python==3.9.7 is currently installed 
Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/home/p.kuznetsov/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [2]:
random.seed(42)

In [3]:
base_path = "./datasets/seg-coco/train"
destination_masks = "./datasets/focused_masks-3"
destination_yolo = "./datasets/yolo-focused-3"
crop_size = 224

In [4]:
transform = A.Compose([
    A.Rotate(limit=(-90, 90), rotate_method="ellipse", p=1, crop_border=False),
    A.HorizontalFlip(p=0.5),
    A.VerticalFlip(p=0.5),
    A.RandomBrightnessContrast(brightness_limit=(-0.2, 0.2), contrast_limit=(-0.3, 0.3), p=0.5),
    A.CLAHE(p=0.15),
    A.OneOf([
        A.GaussianBlur(blur_limit=(3, 3), sigma_limit=(0, 1), p=1),
        A.Blur(blur_limit=(3, 3), p=1),
        A.MedianBlur(blur_limit=3, p=1),
        A.GaussNoise(var_limit=(0.0, 0.01 * 255), p=1),
        A.ElasticTransform(alpha=2, sigma=1, p=1),
        A.RandomFog(fog_coef_range=(0.1, 0.4), p=1),
    ], p=1),
])

rotate = A.Compose([
    A.Rotate(limit=(-90, 90), rotate_method="ellipse", p=1, crop_border=False),
])

random_crop = A.Compose([
    A.RandomCrop(crop_size, crop_size, p=1),
])

In [5]:
json_file = open(f"{base_path}/_annotations.coco.json")
json_data = json.load(json_file)

In [6]:
images = json_data['images']
annotations = json_data['annotations']

In [7]:
data = []
for image in images:
    data.append({
        'id': image['id'],
        'file_name': image['file_name'],
        'segmentation': []
    })

In [8]:
for annotation in annotations:
    for d in data:
        if d['id'] == annotation['image_id']:
            if len(annotation['segmentation']) > 0:
                d['segmentation'].append(np.array(annotation["segmentation"]).reshape((-1, 2)))
            else:
                d['segmentation'].append([])

In [9]:
for d in data:
    image = cv2.imread(f"{base_path}/{d['file_name']}")
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    d['image'] = image

In [10]:
count_dict = {}

for d in data:
    number = d["file_name"].split('_')[0]
    try:
        number = int(number)
    except:
        print(number)
        if -1 in count_dict:
            count_dict[-1] += 1
        else:
            count_dict[-1] = 1
        continue

    if number in count_dict:
        count_dict[number] += 1
    else:
        count_dict[number] = 1

sorted_counts = sorted(count_dict.items(), key=lambda x: x[1], reverse=True)

2022-02-07
2019-10-10
2021-12-29
2021-09-01
2022-09-01
2021-03-19
2021-10-10
2019-12-29
2019-09-01
2021-11-19


In [11]:
test_numbers = []
total = 0
for number, count in sorted_counts:
    if (count > 1 and count < 6) and number not in test_numbers:
        test_numbers.append(number)
        total += count
print(f"Total: {total}")

Total: 163


In [12]:
test_data = []
for d in data:
    try:
        number = int(d["file_name"].split('_')[0])
    except:
        number = -1
    if number in test_numbers:
        test_data.append(d)

In [13]:
import copy
val_data = copy.deepcopy(test_data)

In [14]:
train_data = []
for d in data:
    try:
        number = int(d["file_name"].split('_')[0])
    except:
        number = -1
    if number not in test_numbers:
        train_data.append(d)

In [15]:
def points_to_mask(points, h, w):
    mask = np.zeros((h, w), dtype=np.uint8)
    points = np.round(points).astype(np.int32)
    points = points.reshape((-1, 1, 2))
    cv2.fillPoly(mask, [points], 1)
    return mask

In [16]:
train_rotated = []
for d in train_data:
    for id in range(3):
        image = d['image']
        segmentations = d['segmentation']
        masks = [points_to_mask(s, image.shape[0], image.shape[1]) for s in segmentations]
        
        transformed = rotate(image=image, masks=masks)
        image = transformed['image']
        masks = transformed['masks']

        train_rotated.append({
            'image': image,
            'mask': masks,
            'file_name': f"{d['file_name'].split('.')[0]}_{id}.png"
        })

In [17]:
def crop(image, masks, file_name, crop_size):
    # image, masks, file_name = train_rotated[3]['image'], train_rotated[3]['mask'], train_rotated[3]['file_name']
    width, height = image.shape[1], image.shape[0]
    empty = len(masks) == 0
    result = []
    if empty:
        x_min_valid = 0
        x_max_valid = width - crop_size
        y_min_valid = 0
        y_max_valid = height - crop_size

        crop_x = random.randint(math.ceil(x_min_valid), math.floor(x_max_valid))
        crop_y = random.randint(math.ceil(y_min_valid), math.floor(y_max_valid))

        crop = image[crop_y:crop_y + crop_size, crop_x:crop_x + crop_size]

        result.append({
        'image': crop,
        'mask': [],
        'file_name': file_name
        })
    else:
        id = 0
        for mask in masks:
            x, y = np.where(mask == 1)

            try:
                x_min = min(x)
                x_max = max(x)
                y_min = min(y)
                y_max = max(y)
            except:
                print("empty mask")
                print(mask)
                print(np.sum(mask))
                continue

            # print(x)
            # print(y)
            # print(f"x_min: {x_min}, x_max: {x_max}, y_min: {y_min}, y_max: {y_max}")
            # print(f"width: {width}, height: {height}")

            x_min_valid = max(0, x_max - crop_size)
            x_max_valid = min(width - crop_size, x_min)
            y_min_valid = max(0, y_max - crop_size)
            y_max_valid = min(height - crop_size, y_min)

            if x_min_valid >= x_max_valid or y_min_valid >= y_max_valid or x_max_valid - x_min_valid < 0.5 or y_max_valid - y_min_valid < 0.5:
                print("Invalid crop for image " + file_name)
                print(f"x_min_valid: {x_min_valid}, x_max_valid: {x_max_valid}, y_min_valid: {y_min_valid}, y_max_valid: {y_max_valid}")
                continue

            crop_x = random.randint(math.ceil(x_min_valid), math.floor(x_max_valid))
            crop_y = random.randint(math.ceil(y_min_valid), math.floor(y_max_valid))

            crop = image[crop_y:crop_y + crop_size, crop_x:crop_x + crop_size]
            mask_crops = []
            for inner_mask in masks:
                mask_crop = inner_mask[crop_y:crop_y + crop_size, crop_x:crop_x + crop_size]
                if np.sum(mask_crop) > 0:
                    mask_crops.append(mask_crop)

            result.append({
                'image': crop,
                'mask': mask_crops,
                'file_name': f"{file_name.split('.')[0]}_{id}.png"
            })

            id += 1

    return result

In [18]:
train_cropped = []
for d in train_rotated:
    for id in range(5):
        result = crop(d['image'], d['mask'], f"{d['file_name'].split('.')[0]}_{id}.png", crop_size)
        train_cropped.extend(result)

Invalid crop for image 3_2021-01-31_2021-03-12_png_0_0.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 204
Invalid crop for image 3_2021-01-31_2021-03-12_png_0_1.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 204
Invalid crop for image 3_2021-01-31_2021-03-12_png_0_2.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 204
Invalid crop for image 3_2021-01-31_2021-03-12_png_0_3.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 204
Invalid crop for image 3_2021-01-31_2021-03-12_png_0_4.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 204
Invalid crop for image 3_2021-01-31_2021-03-12_png_1_0.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 166
Invalid crop for image 3_2021-01-31_2021-03-12_png_1_1.png
x_min_valid: 209, x_max_valid: 200, y_min_valid: 0, y_max_valid: 166
Invalid crop for image 3_2021-01-31_2021-03-12_png_1_2.png
x_min_valid: 209, x_max_valid: 200, y_min_val

In [19]:
train_augmented = []
for d in train_cropped:
    for id in range(2):
        augmented = transform(image=d['image'], masks=d['mask'])
        image = augmented['image']
        masks = augmented['masks']

        train_augmented.append({
            'image': image,
            'mask': masks,
            'file_name': d['file_name'].split('.')[0] + f"_{id}.png"
        })

In [20]:
test_cropped = []
for d in test_data:
    image = d['image']
    segmentations = d['segmentation']
    masks = [points_to_mask(s, image.shape[0], image.shape[1]) for s in segmentations]
    
    cropped = crop(d['image'], masks, d['file_name'], crop_size)
    test_cropped.extend(cropped)

Invalid crop for image 104_2022-06-06_2022-07-16_png_jpg.rf.ecaa5d15948988885490e59ddce763e5.jpg
x_min_valid: 841, x_max_valid: 801, y_min_valid: 763, y_max_valid: 823
Invalid crop for image 144_2018-03-12_2018-04-21_png.rf.667b6f7a7cb1e913892662364c0824be.jpg
x_min_valid: 4, x_max_valid: 103, y_min_valid: 0, y_max_valid: 0
Invalid crop for image 104_2022-07-16_2022-08-25_png_jpg.rf.a01a2367a415618e0f05fe0acdf435ee.jpg
x_min_valid: 841, x_max_valid: 801, y_min_valid: 763, y_max_valid: 823
Invalid crop for image 104_2021-10-10_2021-11-19_png_jpg.rf.0e9a8ff6274a36d72df2a6e76d6240e9.jpg
x_min_valid: 841, x_max_valid: 801, y_min_valid: 763, y_max_valid: 823
Invalid crop for image 104_2022-11-12_2022-12-22_png_jpg.rf.250d12cd0dcb07f0e1a4bca259b1a0ae.jpg
x_min_valid: 845, x_max_valid: 798, y_min_valid: 763, y_max_valid: 820


In [21]:
val_cropped = []
for d in val_data:
    image = d['image']
    segmentations = d['segmentation']
    masks = [points_to_mask(s, image.shape[0], image.shape[1]) for s in segmentations]
    
    cropped = crop(d['image'], masks, d['file_name'], crop_size)
    val_cropped.extend(cropped)

Invalid crop for image 104_2022-06-06_2022-07-16_png_jpg.rf.ecaa5d15948988885490e59ddce763e5.jpg
x_min_valid: 841, x_max_valid: 801, y_min_valid: 763, y_max_valid: 823
Invalid crop for image 144_2018-03-12_2018-04-21_png.rf.667b6f7a7cb1e913892662364c0824be.jpg
x_min_valid: 4, x_max_valid: 103, y_min_valid: 0, y_max_valid: 0
Invalid crop for image 104_2022-07-16_2022-08-25_png_jpg.rf.a01a2367a415618e0f05fe0acdf435ee.jpg
x_min_valid: 841, x_max_valid: 801, y_min_valid: 763, y_max_valid: 823
Invalid crop for image 104_2021-10-10_2021-11-19_png_jpg.rf.0e9a8ff6274a36d72df2a6e76d6240e9.jpg
x_min_valid: 841, x_max_valid: 801, y_min_valid: 763, y_max_valid: 823
Invalid crop for image 104_2022-11-12_2022-12-22_png_jpg.rf.250d12cd0dcb07f0e1a4bca259b1a0ae.jpg
x_min_valid: 845, x_max_valid: 798, y_min_valid: 763, y_max_valid: 820


In [22]:
def save(data, folder):
    subdir = os.path.join(destination_masks, folder)
    if not os.path.exists(subdir):
        os.makedirs(subdir)
    for entry in data:
        masks = entry['mask']
        if len(masks) == 0:
            cv2.imwrite(os.path.join(subdir, entry['file_name'].replace(".jpg", ".png")), np.zeros((224, 224), dtype=np.uint8))
        else:
            masks = np.sum(masks, axis=0)
            cv2.imwrite(os.path.join(subdir, entry['file_name'].replace(".jpg", ".png")), masks)

In [23]:
save(train_augmented, "train")
save(test_cropped, "test")
save(val_cropped, "valid")

In [24]:
splits = ["train", "test", "valid"]

for split in splits:
    masks_dir = os.path.join(destination_masks, split)
    target_dir = os.path.join(destination_yolo, split, "labels")
    if not os.path.exists(target_dir):
        os.makedirs(target_dir)
    convert_segment_masks_to_yolo_seg(masks_dir=masks_dir, output_dir=target_dir, classes=2)

Processing datasets/focused_masks-3/train/5_2020-11-19_2020-12-29_png_2_4_0_0.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/5_2020-11-19_2020-12-29_png_2_4_0_0.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/3_2021-03-12_2021-04-21_png_1_2_0_1.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/3_2021-03-12_2021-04-21_png_1_2_0_1.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/120_2021-07-16_2021-08-25_png_jpg_1_0_0_1.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/120_2021-07-16_2021-08-25_png_jpg_1_0_0_1.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/152_2024-03-12_2024-04-21_png_jpg_1_2_0_0.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/152_2024-03-12_2024-04-21_png_jpg_1_2_0_0.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/127_2023-01-31_2023-03-12_png_jpg_1_3_0_0.png imgsz = 224 

Processed and stored at datasets/yolo-focused-3/train/labels/109_2022-04-27_2022-06-06_png_jpg_0_2_0_1.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/6_2022-01-31_2022-03-12_png_2_3_0_0.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/6_2022-01-31_2022-03-12_png_2_3_0_0.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/62_2022-08-25_2022-10-04_png_jpg_0_2_0_0.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/62_2022-08-25_2022-10-04_png_jpg_0_2_0_0.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/128_128_2017-08-25_2017-10-04_png_jpg_0_0_0_0.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/128_128_2017-08-25_2017-10-04_png_jpg_0_0_0_0.txt imgsz = 224 x 224
Processing datasets/focused_masks-3/train/45_2020-03-12_2020-04-21_png_1_2_1_1.png imgsz = 224 x 224
Processed and stored at datasets/yolo-focused-3/train/labels/45_2020-03-12_2020-04-21_p

In [25]:
def save_img(data, folder):
    subdir = os.path.join(destination_yolo, folder, "images")
    if not os.path.exists(subdir):
        os.makedirs(subdir)
    for entry in data:
        image = entry['image']
        file_name = entry['file_name']
        cv2.imwrite(os.path.join(subdir, file_name), cv2.cvtColor(image, cv2.COLOR_RGB2BGR))

In [26]:
save_img(train_augmented, "train")
save_img(test_cropped, "test")
save_img(val_cropped, "valid")

In [28]:
import shutil
shutil.copy("./datasets/data.yaml", f"{destination_yolo}/data.yaml")

'./datasets/yolo-focused-3/data.yaml'

In [28]:
file = "2_2015-10-04_2015-11-13_png_jpg_0_0.png"

In [29]:
import cv2
mask = cv2.imread(f"{destination_masks}/train/{file}")
import matplotlib.pyplot as plt

mask = mask * 1
plt.imshow(mask, cmap='Reds')
print(mask.sum())

[ WARN:0@291.833] global loadsave.cpp:248 findDecoder imread_('./datasets/focused_masks-3/train/2_2015-10-04_2015-11-13_png_jpg_0_0.png'): can't open/read file: check file path/integrity


TypeError: unsupported operand type(s) for *: 'NoneType' and 'int'

In [ ]:
image = cv2.imread(f"{destination_yolo}/train/images/{file}")
image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
image = image * mask
plt.imshow(image)
# plt.imshow(mask, alpha=0.5, vmin=0, vmax=1)